Important link: 
1. https://towardsdatascience.com/understanding-decision-tree-classification-with-scikit-learn-2ddf272731bd
2. https://heartbeat.fritz.ai/implementing-regression-using-a-decision-tree-and-scikit-learn-ac98552b43d7

Decison Trees algorithms can be applied to both regression and classification tasks

In the realm of machine learning decision trees algorithm can be more suitable for regression problems than other common and popular algorithms.
Below are the cases where one would prefer a decision tree over other regression algorithms:

1. There are non-linear or complex relationships between features and labels
2. You need a model that is easy to explain

Decision Trees: Key Terms
1. Root Node: The top-most decision nodel in a decision tree
2. Decision Node: A tree node or parent node that splits into one or more child nodes 
3. Leaf or terminal node: Bottom nodes that(generally speaking) don't split any further
4. Splitting: Process of dividing a node into two or more child nodes
5. Pruning: The opposite process of splitting. Removing the child nodes of a decision node is called pruning.

Regression trees are used when the dependent variable is continuous. <br>
For regression trees, the value of terminal nodes is the mean of the observation falling in that region. Therefore, if an unseen data points falls in that region, we predict using the mean value.

Gini Index : It is a metric to measure how often a randomly chosen element would be incorrectly identified. It means an attribute with lower gini index should be preferred.

Source: https://dataaspirant.com/2017/01/30/how-decision-tree-algorithm-works/

`Overfitting:`
It is a practical problem while building a decision tree model. The model is having an issue of overfitting is considered when the algorithm continues to go deeper and deeper to reduce the training set error but results with an incresed test set error i.e. accuracy of our model goes down. It generally happens when it builds many branches due to outliers and irregularities in data.

Two approaches which can be used to avoid overfitting are:
1. Pre-Pruning
2. Post-Pruning

**Pre-Pruning:**
In pre-pruning, it stops the tree construction bit early. It is preferred not to split a node if its goodness measure is below a threshold value. But it's difficult to choose an appropriate stopping point.

**Post-Pruning:**
In post pruning, it goes deeper and deeper in the tree to build a complete tree. If the tree shows the overfitting problem, then pruning is done as post-prunig step. We use a cross-validation data to check the effects of our pruning. 
Using Cross Validation data, it tests whether expanding a node will make an improvement or not.

If it shows an improvemnt, then we can continue by expanding that node. But if it shows a reduction in accuracy then it should not be expanded i.e. the node should be converted to a leaf node.

In [1]:
# import necessary libraries
import pandas as pd

In [2]:
wineData = pd.read_csv("winequality_red.csv")

In [3]:
wineData.head()

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0            7.4              0.70         0.00             1.9      0.076   
1            7.8              0.88         0.00             2.6      0.098   
2            7.8              0.76         0.04             2.3      0.092   
3           11.2              0.28         0.56             1.9      0.075   
4            7.4              0.70         0.00             1.9      0.076   

   free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                 11.0                  34.0   0.9978  3.51       0.56   
1                 25.0                  67.0   0.9968  3.20       0.68   
2                 15.0                  54.0   0.9970  3.26       0.65   
3                 17.0                  60.0   0.9980  3.16       0.58   
4                 11.0                  34.0   0.9978  3.51       0.56   

   alcohol  quality  
0      9.4        5  
1      9.8        5  
2      9.8        5  
3      9.8        6  
4      9.4        5

In [4]:
wineData.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1599 entries, 0 to 1598
Data columns (total 12 columns):
fixed acidity           1599 non-null float64
volatile acidity        1599 non-null float64
citric acid             1599 non-null float64
residual sugar          1599 non-null float64
chlorides               1599 non-null float64
free sulfur dioxide     1599 non-null float64
total sulfur dioxide    1599 non-null float64
density                 1599 non-null float64
pH                      1599 non-null float64
sulphates               1599 non-null float64
alcohol                 1599 non-null float64
quality                 1599 non-null int64
dtypes: float64(11), int64(1)
memory usage: 150.0 KB


Number of columns = 1599
There is no null value in the columns

In [20]:
X = wineData.drop(columns = "quality")
y = wineData["quality"]

##### Seperate Train and Test Data

In [21]:
# divide the data into train and test set
from sklearn.model_selection import train_test_split
from matplotlib import pyplot as plt

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state =  100)


The parameter test_size is given value 0.2, it means test set will be
20% of the whole dataset and training size will be 80% of the entire dataset. random_state variable is 
a psuedo random number generator state used for random sampling. If you want to
replicate our results, then use the same value of random state

In [22]:
print("Number of training samples:", len(X_train))
print("Number of test samples:", len(X_test))

Number of training samples: 1279
Number of test samples: 320


In [23]:
X_train.head()

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
382             8.3             0.260         0.42             2.0      0.080   
1034            8.9             0.745         0.18             2.5      0.077   
195             7.8             0.590         0.33             2.0      0.074   
370             6.9             0.765         0.02             2.3      0.063   
427             9.5             0.780         0.22             1.9      0.077   

      free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
382                  11.0                  27.0  0.99740  3.21       0.80   
1034                 15.0                  48.0  0.99739  3.20       0.47   
195                  24.0                 120.0  0.99680  3.25       0.54   
370                  35.0                  63.0  0.99750  3.57       0.78   
427                   6.0                  32.0  0.99880  3.26       0.56   

      alcohol  
382       9.4  
1034      9.7  
195       9.4  
370       9.9  
427      10.6

In [24]:
# import decision tree Clasifier from SciKit learn
from sklearn.tree import DecisionTreeClassifier

estimator = DecisionTreeClassifier()

DecisionTree Classifier():<br>
It is the main function for implementing the algorithms. Some important parameters are: <br>
**criterion**-defines the function to measure the quality of a split. Sklearn supports "gini" Index for Gini Index and "Entropy" for Information Gain. By default, it takes "best Value" <br>
**Splitter** - defines the strategy to choose the split at each node. Supports "best" value to choose the best split and "random" to choose the best random split. By default, it takes " best" value <br>
**max_features**: It defines the number of features to consider when looking for the best split. We can input integer, float, string and None value. <br>
<pre>
    If an integer is inputted then it considers that value as max features at each split.
    If float value is taken then it shows the percentage of features at each split.
    If "auto" or "sqrt" is taken then max_features = sqrt(n_features)
    If "log2" is taken then max_features = log2(n_features)
if None, then max_features = n_features. By default, it takes None Value </pre>

**max_depth**- The max_depth parameter denotes maximum depth of the tree. It can take any integer value or none. If None, then nodes are expanded untill all leaves are pure or untill all leaves contain less than min_samples_splt samples. By default, it takes "None" Value.

**min_samples_leaf**: The minimum number of samples requires to be at a leaf node. If an integer value is taken then consider min_samples_leaf as the minimum no. If float, then it shows percentage. By default, it takes "1" value

**max_leaf_nodes** It defines the number of possible leaf nodes. If None, then it takes an unlimited number of leaf nodes. By default, it takes "None" Value.

**min_impurity_split**: It defines the threshold for early stopping tree growth. A node will split if its impurity is above the threshold otherwise it is a leaf.

In [25]:
estimator.fit(X_train, y_train)

DecisionTreeClassifier(ccp_alpha=0.0, class_weight=None, criterion='gini',
                       max_depth=None, max_features=None, max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, presort='deprecated',
                       random_state=None, splitter='best')

In [26]:
data_feature_names = X_train.columns
print(data_feature_names)

Index(['fixed acidity', 'volatile acidity', 'citric acid', 'residual sugar',
       'chlorides', 'free sulfur dioxide', 'total sulfur dioxide', 'density',
       'pH', 'sulphates', 'alcohol'],
      dtype='object')


In [29]:
y.unique()   # Output classes in Target

array([5, 6, 7, 4, 8, 3], dtype=int64)

##### plot the decision tree 

In [31]:
from io import StringIO
from IPython.display import Image
from sklearn.tree import export_graphviz
import pydotplus

dot_data = StringIO()

export_graphviz(estimator, out_file = dot_data, filled = True,
               rounded = True, special_characters= True,
                feature_names= data_feature_names, 
                class_names =['5','6','7','4','8','3'])

graph = pydotplus.graph_from_dot_data(dot_data.getvalue())

graph.write_png('WineDecisionTree.png')

Image(graph.create_png())

Explaining Decision Tree:

In [33]:
# prediction 
# To make predictions, the predict method of the DecisionTreeClassifier class is used.
y_pred = estimator.predict((X_test))

#### Evaluating the Algorithm

In [ ]:
#Now let's compare some of our predicted values with the actual 
#values and see how accurate we were:

In [40]:
df = pd.DataFrame({'Actual': y_test,'Predicted':y_pred})

In [41]:
df.head()

Actual  Predicted
1254       5          6
1087       6          7
822        5          5
1514       6          6
902        7          7

In [ ]:
#Using Scikit library to calculate metrics

In [36]:
from sklearn.metrics import accuracy_score, confusion_matrix

In [37]:
dt_conf_matrix = confusion_matrix(y_test, y_pred)
print(dt_conf_matrix)

[[ 0  0  2  1  0  0]
 [ 0  4  3  5  0  0]
 [ 0  5 94 29  5  0]
 [ 0  4 27 75 31  0]
 [ 0  1  1  8 22  0]
 [ 0  0  0  2  1  0]]


In [39]:
from sklearn.metrics import classification_report
print(classification_report(y_test,y_pred))

              precision    recall  f1-score   support

           3       0.00      0.00      0.00         3
           4       0.29      0.33      0.31        12
           5       0.74      0.71      0.72       133
           6       0.62      0.55      0.58       137
           7       0.37      0.69      0.48        32
           8       0.00      0.00      0.00         3

    accuracy                           0.61       320
   macro avg       0.34      0.38      0.35       320
weighted avg       0.62      0.61      0.61       320



C:\Users\ReeNa\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1272: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [38]:
dt_acc_score = accuracy_score(y_test, y_pred)
print(dt_acc_score*100)

60.9375


In [ ]:
# Understanding F-score

##### Doing Preprocessing and hyperparameters tuning to improve the accuracy.